In [1]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import mutual_info_regression
from sklearn.decomposition import PCA
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from folium import Map, Circle, Marker, Icon
from random import randint
from shapely.geometry import Point

In [3]:
boston_df = pd.read_csv('boston_corrected_corrected.csv')
boston_gdf  = gpd.GeoDataFrame(boston_df, geometry=gpd.points_from_xy(boston_df.LAT, boston_df.LON))

hospital_df = pd.read_csv('massachusetts-hospitals.csv')
hospital_gdf  = gpd.GeoDataFrame(hospital_df, geometry=gpd.points_from_xy(hospital_df.SHAPE_Y, hospital_df.SHAPE_X))

school_df = pd.read_csv('massachusetts-schools-pre-k-through-high-school_new.csv')
school_gdf  = gpd.GeoDataFrame(school_df, geometry=gpd.points_from_xy(school_df.SHAPE_Y, school_df.SHAPE_X))

uni_gdf = gpd.read_file('University_data\GISDATA_COLLEGES_PTPoint.shp')
uni_gdf = uni_gdf.geometry
uni_gdf = uni_gdf.apply(lambda row: Point(row.y, row.x))

train_gdf = gpd.read_file('Train_data\GISDATA_TRAINS_NODEPoint.shp')
train_gdf = train_gdf.geometry
train_gdf = train_gdf.apply(lambda row: Point(row.y, row.x))

chc_gdf = gpd.read_file('Community_Health_Center_data\GISDATA_CHCS_PTPoint.shp')
chc_gdf = chc_gdf.geometry
chc_gdf = chc_gdf.apply(lambda row: Point(row.y, row.x))

boston_gdf.set_crs(epsg=4326, inplace=True)
hospital_gdf.set_crs(epsg=4326, inplace=True)
school_gdf.set_crs(epsg=4326, inplace=True)

boston_gdf = boston_gdf.to_crs(epsg=3857)
hospital_gdf = hospital_gdf.to_crs(epsg=3857)
school_gdf = school_gdf.to_crs(epsg=3857)
uni_gdf = uni_gdf.to_crs(epsg=3857)
train_gdf = train_gdf.to_crs(epsg=3857)
chc_gdf = chc_gdf.to_crs(epsg=3857)

## Checking and cleaning the data

This data frame contains the following columns:

* TOWN a factor with levels given by town names
    * Should all be strings
    * All have capital letter at the beginning of each word

* TOWNNO a numeric vector corresponding to TOWN
    * Should be int
    * Should be same number as number of unique town names

* TRACT a numeric vector of tract ID numbers
    * Should be int
    * Should be >= 0

* LON a numeric vector of tract point longitudes in decimal degrees
    * Should be float
    * Should be between -180 and 180

* LAT a numeric vector of tract point latitudes in decimal degrees
    * Should be float
    * Should be between -90 and 90

* MEDV a numeric vector of median values of owner-occupied housing in USD 1000
    * Should be float

* CMEDV a numeric vector of corrected median values of owner-occupied housing in USD 1000
    * Should be float

* CRIM a numeric vector of per capita crime
    * Should be float

* ZN a numeric vector of proportions of residential land zoned for lots over 25000 sq. ft per town (constant for all Boston tracts)
    * Should be float

* INDUS a numeric vector of proportions of non-retail business acres per town (constant for all Boston tracts)
    * Should be float

* CHAS a factor with levels 1 if tract borders Charles River; 0 otherwise
    * Should be int

* NOX a numeric vector of nitric oxides concentration (parts per 10 million) per town
    * Should be float

* RM a numeric vector of average numbers of rooms per dwelling
    * Should be float

* AGE a numeric vector of proportions of owner-occupied units built prior to 1940
    * Should be float

* DIS a numeric vector of weighted distances to five Boston employment centres
    * Should be float

* RAD a numeric vector of an index of accessibility to radial highways per town (constant for all Boston tracts)
    * Should be float

* TAX a numeric vector full-value property-tax rate per USD 10,000 per town (constant for all Boston tracts)
    * Should be float

* PTRATIO a numeric vector of pupil-teacher ratios per town (constant for all Boston tracts)
    * Should be float

* B a numeric vector of 1000*(Bk - 0.63)^2 where Bk is the proportion of blacks
    * Should be float

* LSTAT a numeric vector of percentage values of lower status population
    * Should be float

Adapted from: https://nowosad.github.io/spData/reference/boston.html

### Checking that there are no null values and that dtypes are as expected

In [4]:
boston_gdf.head()

Unnamed: 0        TOWN  TOWNNO  TRACT        LON        LAT  MEDV  CMEDV  \
0           0      Nahant       0   2011 -70.927800  42.426000  24.0   24.0   
1           1  Swampscott       1   2021 -70.919764  42.481455  21.6   21.6   
2           2  Swampscott       1   2022 -70.897264  42.473777  34.7   34.7   
3           3  Marblehead       2   2031 -70.884407  42.490840  33.4   33.4   
4           4  Marblehead       2   2032 -70.874764  42.499371  36.2   36.2   

      CRIM    ZN  ...    NOX     RM   AGE     DIS  RAD  TAX  PTRATIO       B  \
0  0.00632  18.0  ...  0.538  6.575  65.2  4.0900    1  296     15.3  396.90   
1  0.02731   0.0  ...  0.469  6.421  78.9  4.9671    2  242     17.8  396.90   
2  0.02729   0.0  ...  0.469  7.185  61.1  4.9671    2  242     17.8  392.83   
3  0.03237   0.0  ...  0.458  6.998  45.8  6.0622    3  222     18.7  394.63   
4  0.06905   0.0  ...  0.458  7.147  54.2  6.0622    3  222     18.7  396.90   

   LSTAT                           geometry  
0   4.98  POINT (4722840.716 -11377630.320)  
1   9.14  POINT (4729013.939 -11374893.260)  
2   4.03  POINT (4728159.185 -11367235.395)  
3   2.94  POINT (4730058.638 -11362863.369)  
4   5.33  POINT (4731008.364 -11359586.207)  

[5 rows x 22 columns]

In [5]:
hospital_gdf = hospital_gdf.geometry
hospital_gdf.head()

0    POINT (4747466.578 -11520167.009)
1    POINT (4726668.629 -11423315.492)
2    POINT (4690267.283 -11585327.833)
3    POINT (4703181.401 -11678411.837)
4    POINT (4713250.615 -11438366.700)
Name: geometry, dtype: geometry

In [6]:
school_gdf = school_gdf.geometry
school_gdf.head()

0    POINT (4636965.302 -11379009.899)
1    POINT (4683594.326 -11989720.535)
2    POINT (4678235.601 -11478672.516)
3    POINT (4722150.287 -11409416.711)
4    POINT (4719271.669 -11414830.330)
Name: geometry, dtype: geometry

In [7]:
uni_gdf.head()

0    POINT (4688963.487 -11974293.409)
1    POINT (4690322.055 -11737696.573)
2    POINT (4690165.217 -12046083.251)
3    POINT (4691105.651 -11951920.520)
4    POINT (4691191.197 -11973019.927)
Name: geometry, dtype: geometry

In [8]:
train_gdf.head()

0    POINT (4656409.119 -11545086.256)
1    POINT (4644960.832 -11555266.180)
2    POINT (4766385.674 -11441276.682)
3    POINT (4762342.543 -11432706.794)
4    POINT (4690906.409 -11580898.730)
Name: geometry, dtype: geometry

In [9]:
chc_gdf.head()

0    POINT (4752170.841 -11453943.454)
1    POINT (4714155.422 -11424506.661)
2    POINT (4696904.504 -12263057.239)
3    POINT (4714657.473 -11424050.416)
4    POINT (4645848.910 -11445585.258)
Name: geometry, dtype: geometry

In [10]:
boston_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 506 entries, 0 to 505
Data columns (total 22 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   Unnamed: 0  506 non-null    int64   
 1   TOWN        506 non-null    object  
 2   TOWNNO      506 non-null    int64   
 3   TRACT       506 non-null    int64   
 4   LON         506 non-null    float64 
 5   LAT         506 non-null    float64 
 6   MEDV        506 non-null    float64 
 7   CMEDV       506 non-null    float64 
 8   CRIM        506 non-null    float64 
 9   ZN          506 non-null    float64 
 10  INDUS       506 non-null    float64 
 11  CHAS        506 non-null    int64   
 12  NOX         506 non-null    float64 
 13  RM          506 non-null    float64 
 14  AGE         506 non-null    float64 
 15  DIS         506 non-null    float64 
 16  RAD         506 non-null    int64   
 17  TAX         506 non-null    int64   
 18  PTRATIO     506 non-null    float64 
 19  

In [12]:
sorted(boston_gdf.TOWN.unique())

['Arlington',
 'Ashland',
 'Bedford',
 'Belmont',
 'Beverly',
 'Boston Allston-Brighton',
 'Boston Back Bay',
 'Boston Beacon Hill',
 'Boston Charlestown',
 'Boston Dorchester',
 'Boston Downtown',
 'Boston East Boston',
 'Boston Forest Hills',
 'Boston Hyde Park',
 'Boston Mattapan',
 'Boston North End',
 'Boston Roxbury',
 'Boston Savin Hill',
 'Boston South Boston',
 'Boston West Roxbury',
 'Braintree',
 'Brookline',
 'Burlington',
 'Cambridge',
 'Canton',
 'Chelsea',
 'Cohasset',
 'Concord',
 'Danvers',
 'Dedham',
 'Dover',
 'Duxbury',
 'Everett',
 'Framingham',
 'Hamilton',
 'Hanover',
 'Hingham',
 'Holbrook',
 'Hull',
 'Lexington',
 'Lincoln',
 'Lynn',
 'Lynnfield',
 'Malden',
 'Manchester',
 'Marblehead',
 'Marshfield',
 'Medfield',
 'Medford',
 'Melrose',
 'Middleton',
 'Millis',
 'Milton',
 'Nahant',
 'Natick',
 'Needham',
 'Newton',
 'Norfolk',
 'North Reading',
 'Norwell',
 'Norwood',
 'Peabody',
 'Pembroke',
 'Quincy',
 'Randolph',
 'Reading',
 'Revere',
 'Rockland',
 'Sale

### Check that the characteristics of each column are as expected as defined above

In [13]:
assert len(boston_gdf.TOWN.unique()) == len(boston_gdf.TOWNNO.unique()), 'Number of unique town names must be equal to number of unique town numbers'
assert all(boston_gdf.TRACT) >= 0, 'ID numbers must be greater than or equal to zero'
assert -180 <= all(boston_gdf.LON) <= 180, 'Longitude must be between -180 and 180'
assert -90 <= all(boston_gdf.LAT) <= 90, 'Latitude must be between -90 and 90'

### Dropping the MEDV column as CMEDV will be used as our target variable and we do not want data leakage

In [14]:
boston_gdf.drop('MEDV', axis=1, inplace=True)

### Dropping TOWN because it repeats information in TOWNNO

In [15]:
boston_gdf.drop('TOWN', axis=1, inplace=True)

## Feature engineering

In [21]:
# Create a map
print('INITIALIZING MAP')
m_2 = Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)
print('MAP INITIALIZED')

boston_4326 = boston_gdf.to_crs(epsg=4326)
hospital_4326 = hospital_gdf.to_crs(epsg=4326)
school_4326 = school_gdf.to_crs(epsg=4326)
uni_4326 = uni_gdf.to_crs(epsg=4326)
train_4326 = train_gdf.to_crs(epsg=4326)
chc_4326 = chc_gdf.to_crs(epsg=4326)

colors = []
for _ in range(boston_gdf['TOWNNO'].nunique()):
    colors.append('#%06X' % randint(0, 0xFFFFFF))

print('ADDING HOUSES TO MAP')
for i in range(len(boston_gdf)):
    if i == 8:
        Circle(
            location=[boston_gdf.iloc[i]['LAT'], boston_gdf.iloc[i]['LON']],
            radius=1000,
            color=colors[boston_gdf.iloc[i]['TOWNNO']],
            popup='House '+str(i)+'\n'+str(boston_4326.geometry.iloc[i])).add_to(m_2)
    else:
        Circle(
            location=[boston_gdf.iloc[i]['LAT'], boston_gdf.iloc[i]['LON']],
            radius=10,
            color=colors[boston_gdf.iloc[i]['TOWNNO']],
            popup='House '+str(i)+'\n'+str(boston_4326.geometry.iloc[i])).add_to(m_2)
print('COMPLETE')

print('ADDING HOSPITALS TO MAP')
for i in range(len(hospital_gdf)):
    Marker(
        location=[hospital_4326.iloc[i].x, hospital_4326.iloc[i].y],
        popup = 'Hospital',
        icon=Icon(color="red",icon="h-square", prefix='fa')).add_to(m_2)
print('COMPLETE')
    
print('ADDING SCHOOLS TO MAP')
for i in range(len(school_gdf)):
    Marker(
        location=[school_4326.iloc[i].x, school_4326.iloc[i].y],
        popup='School',
        icon=Icon(color="blue",icon="graduation-cap", prefix='fa')).add_to(m_2)  
print('COMPLETE')

print('ADDING UNIVERSITIES TO MAP')
for i in range(len(uni_gdf)):
    Marker(
        location=[uni_4326.iloc[i].x, uni_4326.iloc[i].y],
        popup='University',
        icon=Icon(color="black",icon="graduation-cap", prefix='fa')).add_to(m_2)  
print('COMPLETE')

print('ADDING TRAIN STATIONS TO MAP')
for i in range(len(train_gdf)):
    Marker(
        location=[train_4326.iloc[i].x, train_4326.iloc[i].y],
        popup='Train station',
        icon=Icon(color="green",icon="train", prefix='fa')).add_to(m_2)  
print('COMPLETE')

print('ADDING HEALTH CENTRES TO MAP')
for i in range(len(chc_gdf)):
    Marker(
        location=[chc_4326.iloc[i].x, chc_4326.iloc[i].y],
        popup='Health Centre',
        icon=Icon(color="orange",icon="medkit", prefix='fa')).add_to(m_2)  
print('COMPLETE')
    
m_2

INITIALIZING MAP
MAP INITIALIZED
ADDING HOUSES TO MAP
COMPLETE
ADDING HOSPITALS TO MAP
COMPLETE
ADDING SCHOOLS TO MAP
COMPLETE
ADDING UNIVERSITIES TO MAP
COMPLETE
ADDING TRAIN STATIONS TO MAP
COMPLETE
ADDING HEALTH CENTRES TO MAP
COMPLETE


In [ ]:
boston_gdf['dist_nearest_hospital'] = [np.inf for _ in range(len(boston_gdf))]
for idx, hospital in hospital_gdf.iterrows():
    boston_gdf['dist_nearest_hospital'] = [min(a,b) for a,b in zip(boston_gdf['dist_nearest_hospital'],
                                              boston_gdf.geometry.distance(hospital.geometry))]

# boston_gdf['number_of_schools_within_1km'] = np.zeros(len(boston_gdf))
boston_gdf['dist_nearest_school'] = [np.inf for _ in range(len(boston_gdf))]
for idx, school in school_gdf.iterrows():
    dist_to_school = boston_gdf.geometry.apply(lambda x: school.geometry.distance(x))
    boston_gdf['dist_nearest_school'] = [min(a,b) for a,b in zip(boston_gdf['dist_nearest_school'], dist_to_school)]
#     boston_gdf['number_of_schools_within_1km'] = [a+1 if dist_to_school[idx] <= 1000 else a for idx, a in enumerate(boston_gdf['number_of_schools_within_1km']) ]
#                                               boston_gdf.geometry.distance(school.geometry))]
#     boston_gdf['dist_nearest_school'] = [min(a,b) for a,b in zip(boston_gdf['dist_nearest_school'],
#                                               boston_gdf.geometry.distance(school.geometry))]

In [ ]:
boston_gdf.iloc[8,:]

In [ ]:
one_km_buffers = boston_gdf.geometry.buffer(1000)
number_of_schools_within_1km = list()
for idx, one_km_buffer in enumerate(one_km_buffers):
    school_count = len(school_gdf.loc[school_gdf.geometry.apply(lambda x: one_km_buffer.contains(x))])
    number_of_schools_within_1km.append(school_count)
    if school_count > 1:
        print('\n \n NEW HOUSE \n ROW NUMBER: '+str(idx)+'\n')
        print('# SCHOOLS ', school_count)#len(school_gdf.loc[school_gdf["geometry"].apply(lambda x: one_km_buffer.contains(x))]))
        print(school_gdf.loc[school_gdf["geometry"].apply(lambda x: one_km_buffer.contains(x)), 'geometry'].to_crs(epsg='4326'))
        print(boston_gdf.to_crs(epsg='4326').geometry.iloc[idx])
boston_gdf['number_of_schools_within_1km'] = number_of_schools_within_1km
#     if school_count > 1:
#         print('\n \n NEW HOUSE \n ROW NUMBER: '+str(idx)+'\n')
#         print('# SCHOOLS ', school_count)#len(school_gdf.loc[school_gdf["geometry"].apply(lambda x: one_km_buffer.contains(x))]))
#         print(school_gdf.loc[school_gdf["geometry"].apply(lambda x: one_km_buffer.contains(x)), 'geometry'].to_crs(epsg='4326'))
#         print(boston_gdf.to_crs(epsg='4326').geometry.iloc[idx])

In [ ]:
boston_gdf.describe()

### Seperate explanatory variables from target and split into train and test set (80:20), will be using cross-validation on training set

In [ ]:
X = boston_gdf.copy()
y = X.pop('CMEDV')

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2021)

### Calculate a mutual information score to understand how knowledge of one quantity reduces uncertainty about the target variable

* 0 means that the quantities are independent
* The higher the score the better
* Scores > 2 are uncommon as mutual information score increases slowly as it is a logarithmic quantity

In [ ]:
mi_scores = mutual_info_regression(X.loc[:, X.columns != 'geometry'], y, random_state=2021)
mi_scores_series = pd.Series(mi_scores, name="MI Scores", index=X.loc[:, X.columns != 'geometry'].columns).sort_values(ascending=False)

In [ ]:
mi_scores_series

In [ ]:
mi_scores_series.plot.barh()
plt.xlabel('Mutual Information Score')
plt.ylabel('Feature')
plt.show()

### Correlation coefficients

In [ ]:
%matplotlib inline
fig, ax = plt.subplots(figsize=(15,15))
cm = np.corrcoef(X_train.loc[:, X.columns != 'geometry'].values.T)
sns.set(font_scale=1.5)
hm = sns.heatmap(cm,
                cbar=True,
                annot=True,
                square=True,
                fmt='.2f',
                annot_kws={'size': 15},
                yticklabels=X_train.loc[:, X.columns != 'geometry'].columns,
                xticklabels=X_train.loc[:, X.columns != 'geometry'].columns,
                ax=ax)

### Normalizing data using StandardScaler()

In [ ]:
x_scaler = StandardScaler()
X_train_sc = x_scaler.fit_transform(X_train.loc[:, X.columns != 'geometry'])
X_test_sc = x_scaler.transform(X_test.loc[:, X.columns != 'geometry'])

### Principle Component Analysis (PCA)

In [ ]:
pca = PCA()
X_train_pca = pca.fit_transform(X_train_sc)

component_names = [f"PC{i+1}" for i in range(X_train_pca.shape[1])]
X_train_pca_df = pd.DataFrame(X_train_pca, columns=component_names)

X_train_pca_df.head()

In [ ]:
loadings = pd.DataFrame(
    pca.components_.T,  # transpose the matrix of loadings
    columns=component_names,  # so the columns are the principal components
    index=X_train.loc[:, X.columns != 'geometry'].columns,  # and the rows are the original features
)
loadings = pd.concat([loadings, pd.DataFrame(X_train.loc[:, X.columns != 'geometry'].columns, columns=['col_names'], index=X_train.loc[:, X.columns != 'geometry'].columns)], axis=1)

In [ ]:
loadings.head()

In [ ]:
plt.figure(figsize=(20,10))
plt.bar(component_names, pca.explained_variance_ratio_)

In [ ]:
%matplotlib inline

fg = sns.FacetGrid(data=loadings, hue='col_names', hue_order=X_train.loc[:, X.columns != 'geometry'].columns, height=8)
fg.map(plt.scatter, 'PC1', 'PC2').add_legend(ncol=1)
for x, y, label in zip(loadings.PC1, loadings.PC2, loadings.col_names):
    plt.text(x=x+0.01, y=y+0.01, s=label)

### Benchmark model: Linear Regression

In [ ]:
def mean_absolute_percentage_error(true, predicted):
    return np.mean(abs((true-predicted)/true))*100

In [ ]:
benchmark_model = LinearRegression(n_jobs=-1)
benchmark_model.fit(X_train_sc, y_train)
train_pred = benchmark_model.predict(X_train_sc)
train_RMSE = mean_squared_error(y_train, train_pred, squared=False)
train_MAPE = mean_absolute_percentage_error(y_train, train_pred)
test_pred = benchmark_model.predict(X_test_sc)
test_RMSE = mean_squared_error(y_test, test_pred, squared=False)
test_MAPE = mean_absolute_percentage_error(y_test, test_pred)

In [ ]:
benchmark_res = {'train_RMSE':[train_RMSE], 'test_RMSE':[test_RMSE], 'train_MAPE':[train_MAPE], 'test_MAPE':[test_MAPE]}
evaluation = pd.DataFrame(benchmark_res, index=['benchmark'])

In [ ]:
evaluation

In [ ]:
# can try decision tree regressor